# Fine-Tuning GPT-2 with RLHF on Drugs.com Reviews for High-Quality Drug Reviews on Depression


**Author**: Zakia Salod

**Affiliation**: University of KwaZulu-Natal (UKZN), Durban, South Africa

**Contact**: zakia.salod@gmail.com

**Machine Used**: Google Colab T4 GPU

**Last Updated**: 10 December 2023

**Description**:
This notebook demonstrates fine-tuning the GPT-2 model (specifically, Zakia/gpt2-drugscom_depression_reviews) using Reinforcement Learning with Human Feedback (RLHF), leveraging the TRL (transformer reinforcement learning) library. The base model (GPT-2) and reward model (DistilBERT, specifically, Zakia/distilbert-drugscom_depression_reviews) are both fine-tuned on the same Drugs.com reviews dataset, focusing on depression. The goal is to further refine the GPT-2 model's ability to generate high-quality patient reviews on depression drugs, using RLHF for targeted improvement. This approach aims to harness the strengths of both GPT-2 and DistilBERT in generating insightful and accurate text content.


**License**:
This work is licensed under the [Apache 2.0 License](https://www.apache.org/licenses/LICENSE-2.0). Free for educational and research use.



<div style="text-align: center">
  <img src='https://huggingface.co/Zakia/gpt2-drugscom_depression_reviews-hq-v1/resolve/main/images/RLHF_DepressionReviews_Flow.png' width='800'>
  <p style="text-align: center;">
    <b>Figure 1:</b> This diagram represents the RLHF process applied to the GPT-2 model (<a href="https://huggingface.co/Zakia/gpt2-drugscom_depression_reviews-hq-v1">link</a>) using the DrugsCom DepressionReviews dataset. The fine-tuned GPT-2 model (<a href="https://huggingface.co/Zakia/gpt2-drugscom_depression_reviews">link</a>) shown in purple, DistilBERT model (<a href="https://huggingface.co/Zakia/distilbert-drugscom_depression_reviews">link</a>) depicted in orange, and the dataset (<a href="https://huggingface.co/datasets/Zakia/drugscom_reviews">link</a>, filtered for 'Depression' condition in the 'train' set) mentioned in the turquoise box, are highlighted to show their integration in the fine-tuning process.</p></div>

## STEP 1: SETTING UP THE ENVIRONMENT

### Load Necessary Libraries

In [ ]:
# Enable automatic module reloading to reflect changes in external .py files
%load_ext autoreload
# Reload all modules before executing code, keeping modules up-to-date
%autoreload 2

### Install Required Packages

In [ ]:
!pip install Accelerator peft trl wandb

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.3/168.3 kB 24.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 133.9/133.9 kB 19.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 32.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.2/90.2 kB 13.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.7/57.7 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.7/265.7 kB 34.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 53.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.9/100.9 kB 15.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.6/190.6 kB 25.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 252.8/252.8 kB 32.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 9.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━

### Import Necessary Libraries

In [ ]:
from dataclasses import dataclass, field
from typing import Optional
import pandas as pd
import re
import html
import numpy as np
import random

import torch
from accelerate import Accelerator
from datasets import load_dataset
from peft import LoraConfig
from tqdm import tqdm
from transformers import AutoTokenizer, pipeline
from datasets import concatenate_datasets

from trl import AutoModelForCausalLMWithValueHead, AutoModelForSeq2SeqLMWithValueHead, PPOConfig, PPOTrainer, set_seed
from trl.core import LengthSampler
from trl.import_utils import is_xpu_available

/usr/local/lib/python3.10/dist-packages/trl/trainer/ppo_config.py:141: UserWarning: The `optimize_cuda_cache` arguement will be deprecated soon, please use `optimize_device_cache` instead.
  warnings.warn(


In [ ]:
tqdm.pandas()

### Set Random Seeds for Reproducibility

In [ ]:
seed_value = 42

random.seed(seed_value)
torch.manual_seed(seed_value)

### Initialize Weights & Biases for Tracking

In [ ]:
import wandb

wandb.init(project="gpt2-drugscom_depression_reviews-hq-v1")

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


## STEP 2: CONFIGURATION

### Define script arguments for training configuration

In [ ]:
@dataclass
class ScriptArguments:
    ppo_config: PPOConfig = field(
        default_factory=lambda: PPOConfig(
            model_name="Zakia/gpt2-drugscom_depression_reviews",
            query_dataset="Zakia/drugscom_reviews",
            reward_model="sentiment-analysis:Zakia/distilbert-drugscom_depression_reviews",
            learning_rate=1.41e-5,
            log_with="wandb",
            mini_batch_size=128,
            batch_size=128,
            gradient_accumulation_steps=1,
            early_stopping=False,
            target_kl=6.0,
            kl_penalty="kl",
            seed=0,
            use_score_scaling=False,
            use_score_norm=False,
            score_clip=None,
        )
    )
    use_seq2seq: bool = False
    """whether to use seq2seq models"""
    use_peft: bool = False
    """whether to use peft"""
    peft_config: Optional[LoraConfig] = field(
        default_factory=lambda: LoraConfig(
            r=16,
            lora_alpha=16,
            bias="none",
            task_type="CAUSAL_LM",
        ),
    )
    trust_remote_code: bool = field(default=False, metadata={"help": "Enable `trust_remote_code`"})

### Initialize script arguments

In [ ]:
args = ScriptArguments(
    ppo_config=PPOConfig(
        model_name="Zakia/gpt2-drugscom_depression_reviews",
        query_dataset="Zakia/drugscom_reviews",
        reward_model="sentiment-analysis:Zakia/distilbert-drugscom_depression_reviews",
        learning_rate=1.41e-5,
        log_with="wandb",
        mini_batch_size=128,
        batch_size=128,
        gradient_accumulation_steps=1,
        early_stopping=False,
        target_kl=6.0,
        kl_penalty="kl",
        seed=0,
        use_score_scaling=False,
        use_score_norm=False,
        score_clip=None,
    ),
    use_seq2seq=False,
    use_peft=False,
    peft_config=LoraConfig(
        r=16,
        lora_alpha=16,
        bias="none",
        task_type="CAUSAL_LM",
    ),
    trust_remote_code=False
)

In [ ]:
# We then define the arguments to pass to the sentiment analysis pipeline.
# We set `return_all_scores` to True to get the sentiment score for each token.
sent_kwargs = {"return_all_scores": True, "function_to_apply": "none", "batch_size": 16}

# Select appropriate model class based on arguments
trl_model_class = AutoModelForCausalLMWithValueHead if not args.use_seq2seq else AutoModelForSeq2SeqLMWithValueHead

## STEP 3: DATASET PREPARATION

In [ ]:
# Function to clean review text
def clean_review(text):
    # Check if the text is a string
    if not isinstance(text, str):
      return ""  # Return an empty string if the input is not a string
    text = html.unescape(text)  # Decode HTML entities
    text = re.sub(r'"', '', text)  # Remove quotes
    text = re.sub(r'<.*?>', '', text)  # Remove HTML tags
    return text

In [ ]:
# Clean the reviews of the dataset
# Apply the clean_review function in a batched manner
def clean_reviews(batch):
    # Apply clean_review to each review in the batch and return the modified batch
    return {"review": [clean_review(review) for review in batch["review"]]}

In [ ]:
# Function to build and preprocess the dataset
def build_dataset(config, query_dataset, input_min_text_length=2, input_max_text_length=8):
    """
    Build dataset for training. This builds the dataset from `load_dataset`

    Args:
        query_dataset (`str`):
            The name of the dataset to be loaded.

    Returns:
        dataloader (`torch.utils.data.DataLoader`):
            The dataloader for the dataset.
    """
    tokenizer = AutoTokenizer.from_pretrained(config.model_name)
    tokenizer.pad_token = tokenizer.eos_token

    # Load the dataset
    ds = load_dataset(query_dataset, split="train")

    # Filter the dataset for the condition 'Depression'
    ds = ds.filter(lambda x: x["condition"] == "Depression")

    # Filter out (remove) rows with missing drugName, or review
    ds = ds.filter(lambda x: all([x.get("drugName"), x.get("review")]))

    # Clean the reviews
    ds = ds.map(clean_reviews, batched=True)

    # Get the number of records
    num_records = ds.num_rows
    print(f"Number of records with Depression condition: {num_records}")

    input_size = LengthSampler(input_min_text_length, input_max_text_length)

    # Tokenization
    def tokenize(sample):
        sample["input_ids"] = tokenizer.encode(sample["review"])[: input_size()]
        sample["query"] = tokenizer.decode(sample["input_ids"])
        return sample

    ds = ds.map(tokenize, batched=False)

    ds.set_format(type="torch")
    return ds

In [ ]:
# Load and preprocess the dataset
# We retrieve the dataloader by calling the `build_dataset` function.
dataset = build_dataset(args.ppo_config, args.ppo_config.query_dataset)

tokenizer_config.json:   0%|          | 0.00/525 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/999k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/470 [00:00<?, ?B/s]

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

...

Filter:   0%|          | 0/161297 [00:00<?, ? examples/s]

Filter:   0%|          | 0/9069 [00:00<?, ? examples/s]

Map:   0%|          | 0/9069 [00:00<?, ? examples/s]

Number of records with Depression condition: 9069


Map:   0%|          | 0/9069 [00:00<?, ? examples/s]

## STEP 4: MODEL INITIALIZATION

In [ ]:
def collator(data):
    return dict((key, [d[key] for d in data]) for key in data[0])

In [ ]:
# Set seed before initializing value head for deterministic eval
set_seed(args.ppo_config.seed)

In [ ]:
# Now let's build the model, the reference model, and the tokenizer.
if not args.use_peft:
    ref_model = trl_model_class.from_pretrained(args.ppo_config.model_name, trust_remote_code=args.trust_remote_code)
    device_map = None
    peft_config = None
else:
    peft_config = args.peft_config
    ref_model = None
    # Copy the model to each device
    device_map = {"": Accelerator().local_process_index}

config.json:   0%|          | 0.00/942 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/498M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

In [ ]:
model = trl_model_class.from_pretrained(
    args.ppo_config.model_name,
    trust_remote_code=args.trust_remote_code,
    device_map=device_map,
    peft_config=peft_config,
)

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(args.ppo_config.model_name)

In [ ]:
# Some tokenizers like GPT-2's don't have a padding token by default, so we set one here.
tokenizer.pad_token_id = tokenizer.eos_token_id

## STEP 5: INITIALIZE PPO TRAINER

In [ ]:
# We then build the PPOTrainer, passing the model, the reference model, the tokenizer
ppo_trainer = PPOTrainer(args.ppo_config, model, ref_model, tokenizer, dataset=dataset, data_collator=collator)

In [ ]:
# We then build the sentiment analysis pipeline, passing the model name and the
# sentiment analysis pipeline arguments. Let's also make sure to set the device
# to the same device as the PPOTrainer.
device = ppo_trainer.accelerator.device
if ppo_trainer.accelerator.num_processes == 1:
    if is_xpu_available():
        device = "xpu:0"
    else:
        device = 0 if torch.cuda.is_available() else "cpu"  # to avoid a `pipeline` bug
ds_plugin = ppo_trainer.accelerator.state.deepspeed_plugin
task, model_name = args.ppo_config.reward_model.split(":")
if ds_plugin is not None and ds_plugin.is_zero3_init_enabled():
    with ds_plugin.zero3_init_context_manager(enable=False):
        sentiment_pipe = pipeline(task, model=model_name, device=device)
else:
    sentiment_pipe = pipeline(task, model=model_name, device=device)

config.json:   0%|          | 0.00/781 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/268M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.25k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

In [ ]:
# Some tokenizers like GPT-2's don't have a padding token by default, so we set one here.
if sentiment_pipe.tokenizer.pad_token_id is None:
    sentiment_pipe.tokenizer.pad_token_id = tokenizer.pad_token_id

if sentiment_pipe.model.config.pad_token_id is None:
    sentiment_pipe.model.config.pad_token_id = tokenizer.pad_token_id

In [ ]:
text = "This medication has changed my life for the better. I've experienced no side effects and my symptoms of depression have significantly decreased."
sentiment_pipe(text, **sent_kwargs)

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/text_classification.py:105: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(


[[{'label': 'LOW_QUALITY_REVIEW', 'score': -2.689751625061035},
  {'label': 'HIGH_QUALITY_REVIEW', 'score': 2.4064526557922363}]]

In [ ]:
text = "I've had a terrible experience with this medication. It made me feel nauseous and I didn't notice any improvement in my condition."
sentiment_pipe(text, **sent_kwargs)

[[{'label': 'LOW_QUALITY_REVIEW', 'score': 3.4417612552642822},
  {'label': 'HIGH_QUALITY_REVIEW', 'score': -3.960636615753174}]]

### Generation Settings
For the response generation we just use sampling and make sure top-k and nucleus sampling are turned off as well as a minimal length.

In [ ]:
# We then define the arguments to pass to the `generate` function. These arguments
# are passed to the `generate` function of the PPOTrainer, which is a wrapper around
# the `generate` function of the trained model.
generation_kwargs = {
    "min_length": -1,
    "top_k": 0.0,
    "top_p": 1.0,
    "do_sample": True,
    "pad_token_id": tokenizer.eos_token_id,
    "max_new_tokens": 32,
}

## STEP 6: TRAINING LOOP FOR FINE-TUNING WITH REINFORCEMENT LEARNING WITH HUMAN FEEDBACK (RLHF)

In [ ]:
# Training loop for RLHF
for epoch, batch in tqdm(enumerate(ppo_trainer.dataloader)):
    query_tensors = batch["input_ids"]

    # Get response from gpt2
    response_tensors, ref_response_tensors = ppo_trainer.generate(
        query_tensors, return_prompt=False, generate_ref_response=True, **generation_kwargs
    )
    batch["response"] = tokenizer.batch_decode(response_tensors)
    batch["ref_response"] = tokenizer.batch_decode(ref_response_tensors)

    # Compute sentiment score
    texts = [q + r for q, r in zip(batch["query"], batch["response"])]
    pipe_outputs = sentiment_pipe(texts, **sent_kwargs)
    rewards = [torch.tensor(output[1]["score"]) for output in pipe_outputs]
    ref_texts = [q + r for q, r in zip(batch["query"], batch["ref_response"])]
    ref_pipe_outputs = sentiment_pipe(ref_texts, **sent_kwargs)
    ref_rewards = [torch.tensor(output[1]["score"]) for output in ref_pipe_outputs]
    batch["ref_rewards"] = ref_rewards

    # Run PPO step
    stats = ppo_trainer.step(query_tensors, response_tensors, rewards)
    ppo_trainer.log_stats(stats, batch, rewards, columns_to_log=["query", "response", "ref_response", "ref_rewards"])

0it [00:00, ?it/s]You're using a GPT2TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.
4it [02:48, 41.74s/it]/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(
70it [46:05, 39.51s/it]


## TRAINING PROGRESS WITH WEIGHTS & BIASES

This section of the notebook is dedicated to visualizing and interpreting the training progress using the Weights & Biases platform. By integrating with Weights & Biases, we gain access to valuable visual insights that help us understand how the model's performance evolves over time. Refer to the interactive report on wandb.ai at: [GPT-2 RLHF DepressionReviews Report](https://wandb.ai/team-zakia/trl/reports/GPT-2-RLHF-DepressionReviews-Report--Vmlldzo2MjMxNjk5?accessToken=2bjrzj5pa1rspudwgw38hgv0rqamtpfgd30feha7vkzht01hkrytet9vy82x2rvk). An overview of the Reward Mean Plot and the Reward Distribution Heatmap Plot from this report can be found below, with the plots in Figures 2 and 3, respectively.

### Reward Mean Plot

<div style="text-align: center">
<img src='https://huggingface.co/Zakia/gpt2-drugscom_depression_reviews-hq-v1/resolve/main/images/reward_mean_plot.png' width='800'>
<p style="text-align: center;"> <b>Figure 2:</b> env/reward_mean plot showing the average reward per training step. </p>
</div>

This plot represents the average reward that the model received at each step of the training process. A reward in this context is a numerical value that indicates how well the generated text aligns with high-quality standards as determined by the reward model. The upward trend in the plot suggests that the model consistently starts to generate more positive and aligned outputs as training progresses, indicating that the RLHF technique is effectively improving the model's performance.

### Reward Distribution Heatmap Plot

<div style="text-align: center">
<img src='https://huggingface.co/Zakia/gpt2-drugscom_depression_reviews-hq-v1/resolve/main/images/reward_distribution_heatmap.png' width='800'>
<p style="text-align: center;"> <b>Figure 3:</b> env/reward_dist heatmap plot showing the distribution of rewards over training steps. </p>
</div>

This heatmap illustrates the distribution of rewards over training steps. Each vertical slice of the plot can be thought of as a snapshot of the reward landscape at a given step, with the color intensity representing the frequency of rewards at different levels. As the training continues, we expect to see the color bands shift upwards, which would indicate that the model is more frequently generating higher-quality responses.

## STEP 7: EVALUATE THE MODEL

In [ ]:
output_min_length = 10
output_max_length = 50
output_length_sampler = LengthSampler(output_min_length, output_max_length)

#### Get a batch from the dataset
bs = 20
game_data = dict()
dataset.set_format("pandas")
df_batch = dataset[:].sample(bs)
game_data["query"] = df_batch["query"].tolist()
query_tensors = df_batch["input_ids"].tolist()

response_tensors_ref, response_tensors = [], []

#### Get response from GPT2 and GPT2_REF
for i in range(bs):
    gen_len = output_length_sampler()

    # Update generation_kwargs with the dynamic max_new_tokens value
    dynamic_generation_kwargs = generation_kwargs.copy()
    dynamic_generation_kwargs['max_new_tokens'] = gen_len

    output = ref_model.generate(
        torch.tensor(query_tensors[i]).unsqueeze(dim=0).to(device), **dynamic_generation_kwargs
    ).squeeze()[-gen_len:]
    response_tensors_ref.append(output)

    output = model.generate(
        torch.tensor(query_tensors[i]).unsqueeze(dim=0).to(device), **dynamic_generation_kwargs
    ).squeeze()[-gen_len:]
    response_tensors.append(output)

#### Decode responses
game_data["response (before)"] = [tokenizer.decode(response_tensors_ref[i]) for i in range(bs)]
game_data["response (after)"] = [tokenizer.decode(response_tensors[i]) for i in range(bs)]

#### Sentiment analysis of query/response pairs before/after
texts = [q + r for q, r in zip(game_data["query"], game_data["response (before)"])]
game_data["rewards (before)"] = [output[1]["score"] for output in sentiment_pipe(texts, **sent_kwargs)]

texts = [q + r for q, r in zip(game_data["query"], game_data["response (after)"])]
game_data["rewards (after)"] = [output[1]["score"] for output in sentiment_pipe(texts, **sent_kwargs)]

# Store results in a dataframe
df_results = pd.DataFrame(game_data)
df_results

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/text_classification.py:105: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


query  \
0         Very Very good. Helps   
1           It worked for about   
2                 Started on 20   
3                     I am a 43   
4                  I got on Pro   
5      This drug has changed me   
6    Good Med! Little skeptical   
7             I used to take cl   
8                Been on Prozac   
9                  I've been on   
10   I've been taking this pill   
11             Was put on 30mg.   
12            I was addicted to   
13   I've been on approximately   
14   Super good for depression.   
15       Hyped me up like crazy   
16                    I am a 32   
17  My only complaint is that I   
18                 I've been on   
19             Lexapro has been   

                                    response (before)  \
0   Very Very good. Helps to deal with some of the...   
1    a month. The nausea is gone and I no longer f...   
2    mg.  It seems to help somewhat with some of t...   
3    year old woman with severe anxiety and depres...   
4   zac.  I would sleep all night, feel sick one d...   
5    drastically.  A year after taking an XL I bec...   
6    at first, because some things that seem so go...   
7     onazepam for 4 years and that caused much worse   
8    for 11 years now and still getting worse as t...   
9    Pristiq for 1 week now. The first 1 day was h...   
10     for 6 months and I feel 100% better after just   
11   Still depressed the first 3 months. Now I'm o...   
12   opiates for years when I was younger and I co...   
13   10 mg for six months and it's taking away som...   
14  Super good for depression.  Diarrhea is better...   
15  , as did my MGs who said they thought this was...   
16  Y male and have been on up to 300 mg of zoloft...   
17   complaint is that I experience extreme foggy ...   
18   this 300mg for just a little over a year and ...   
19   better than anything I've tried to battle my ...   

                                     response (after)  rewards (before)  \
0    me with extreme depression and anxiety. Can h...         -1.911440   
1    6 months and I feel so much better that I've ...          1.584692   
2   mg for 4 days now...I feel great. I've been si...         -3.230841   
3    year old mother of two and a mother of two da...          0.613143   
4   I got on Prozac for about two years. Prozac re...         -3.422938   
5    from an excited procrastinator! I feel like I...         -3.109789   
6     Good Med! Little skeptical & SEXy!<|endoftext|>         -3.691891   
7                 onazepam and 5mg prozac at the same         -1.095920   
8    for 13 years. I have never felt this good in ...         -1.745274   
9   I've been on this for over three months, I fee...         -0.377317   
10         for almost 14 years and I took I F 3 times          1.914182   
11   It made me feel much better! I could finally ...         -3.148672   
12   SSRI's, hallucinogens, and drug- just therapy...         -3.175338   
13   two dozen different SSRI's over the past thir...         -3.352825   
14  Super good for depression. I am 5'1 and I have...          1.200642   
15   before and I'm a great mom now! I work as an ...         -4.075667   
16  yr old male and live in a very nice suburb (wi...          0.437383   
17   feel fatigued during the day. And also depres...         -4.083458   
18  I've been on this anti-depressant for over 18 ...         -0.072659   
19  Lexapro has been AMAZING, so far. I've been on...         -1.699961   

    rewards (after)  
0          2.428029  
1          2.306569  
2          2.124902  
3          2.237940  
4          2.157211  
5          0.991710  
6         -1.087502  
7          1.416539  
8          2.083820  
9          2.041740  
10         2.104877  
11         2.363128  
12         0.608868  
13         2.426083  
14         1.900504  
15         1.796120  
16         2.238822  
17        -3.843148  
18         0.724089  
19         1.292072

Looking at the reward mean/median of the generated sequences we observe a significant difference.

In [ ]:
print("mean:")
display(df_results[["rewards (before)", "rewards (after)"]].mean())
print()
print("median:")
display(df_results[["rewards (before)", "rewards (after)"]].median())

mean:


rewards (before)   -1.622197
rewards (after)     1.415619
dtype: float64


median:


rewards (before)   -1.828357
rewards (after)     2.062780
dtype: float64

## STEP 8: SAVE THE FINE-TUNED GPT-2 MODEL: gpt2-drugscom_depression_reviews-hq-v1

In [ ]:
from huggingface_hub import notebook_login # To log to our Hugging Face account to be able to upload models to the Hub.

In [ ]:
# Login to Hugging Face within the notebook
notebook_login()
!git config --global credential.helper store

NotImplementedError: ignored

In [ ]:
# Save and push your model to the hub
model.save_pretrained("gpt2-drugscom_depression_reviews-hq-v1", push_to_hub=True)
tokenizer.save_pretrained("gpt2-drugscom_depression_reviews-hq-v1", push_to_hub=True)

model.safetensors:   0%|          | 0.00/498M [00:00<?, ?B/s]

('gpt2-drugscom_depression_reviews-hq-v1/tokenizer_config.json',
 'gpt2-drugscom_depression_reviews-hq-v1/special_tokens_map.json',
 'gpt2-drugscom_depression_reviews-hq-v1/vocab.json',
 'gpt2-drugscom_depression_reviews-hq-v1/merges.txt',
 'gpt2-drugscom_depression_reviews-hq-v1/added_tokens.json',
 'gpt2-drugscom_depression_reviews-hq-v1/tokenizer.json')